In [20]:
#import modules
import pandas as pd
import datetime as dt
import numpy as np
import matplotlib
import matplotlib.pyplot as plt 
import seaborn as sns
import sklearn

from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import cross_val_predict
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.utils import resample

pd.options.display.max_columns=999
pd.options.display.max_rows=3000
import numpy as np

In [3]:

from openpyxl.workbook import Workbook


In [4]:
df = pd.read_excel('Collections Case Study Data.xlsx', sheet_name=None)

In [6]:
df.keys()

odict_keys(['Loan Details', 'Loan_Status_MartoMay', 'Loan_Status_AprtoJun', 'Historical 6 Months Details', 'Loan_ID mapping', 'Call Details'])

In [7]:
for i in df.keys():
    print(i)
    print(df[i].head())
    print('\n')
    print('\n')

Loan Details
      Loan_id  Debt_to_burden_Ratio  total_income  TENURE  Sanctioned Amount
0  A999993387              0.259113     5326806.0      36           22000000
1  A999990339              0.323385     8392773.0      48           73000000
2  A999971854              0.346267    12000000.0      48           80000000
3  A999952066              0.229800     9000000.0      36           50000000
4  A999938479              0.370082     8500000.0      36           67000000




Loan_Status_MartoMay
      Loan_id Bucket  TENURE  PRINBALANCE  Months on Books  Sanctioned Amount  \
0  A999993387    TB0      36   13785200.0               18           22000000   
1  A999993387    TB0      36   14361500.0               17           22000000   
2  A999990339    TB0      48   68114900.0                6           73000000   
3  A999990339    TB0      48   68957500.0                5           73000000   
4  A999990339    TB0      48   69805500.0                4           73000000   

   Month  Unn

In [8]:
mar_data = df['Loan_Status_MartoMay'].loc[df['Loan_Status_MartoMay']['Month'] == 'March']
mar_hist_data = df['Historical 6 Months Details'].loc[df['Historical 6 Months Details']['Month'] == 'March']

In [9]:
mar_data_1 = pd.merge(mar_data, mar_hist_data, how='left', on='Loan_id', suffixes=('_mar', '_mar'))

In [10]:
mar_data_1.head()

Loan_id Bucket  TENURE  PRINBALANCE  Months on Books  Sanctioned Amount  \
0  A999993387    TB0      36   14361500.0               17           22000000   
1  A999990339    TB0      48   69805500.0                4           73000000   
2  A999952066    TB0      36   37728800.0               12           50000000   
3  A999937745    TB0      36   45753500.0                3           48000000   
4  A999873098    TB0      48   42680200.0               12           50000000   

  Month_mar  Unnamed: 7  Unnamed: 8  paidcure  paiduncure  unpaid  rollb  \
0     March         NaN    576300.0         6           0       0      0   
1     March         NaN    848000.0         4           0       0      0   
2     March         NaN   1237600.0         6           0       0      0   
3     March         NaN         NaN         3           0       1      0   
4     March         NaN         NaN         6           0       0      0   

   rollf  num6mosdel  num3mosdel  num6mosdel_2plus  num3mosdel_2plus  max6del  \
0      0           0           0                 0                 0        0   
1      0           0           0                 0                 0        0   
2      0           0           0                 0                 0        0   
3      0           0           0                 0                 0        0   
4      0           0           0                 0                 0        0   

   max3del Month_mar  
0        0     March  
1        0     March  
2        0     March  
3        0     March  
4        0     March

In [11]:
mar_data_1[mar_data_1['paidcure'].isnull()]

Empty DataFrame
Columns: [Loan_id, Bucket, TENURE, PRINBALANCE, Months on Books, Sanctioned Amount, Month_mar, Unnamed: 7, Unnamed: 8, paidcure, paiduncure, unpaid, rollb, rollf, num6mosdel, num3mosdel, num6mosdel_2plus, num3mosdel_2plus, max6del, max3del, Month_mar]
Index: []

In [12]:
jun_data = df['Loan_Status_AprtoJun'].loc[df['Loan_Status_AprtoJun']['Month'] == 'June']

In [13]:
len(jun_data)

29115

In [14]:
jun_data.head()

Loan_id   Bucket  PRINBALANCE  TENURE  Months on Books  \
2   A999990339  REGULAR   66303700.0      48                7   
5   A999971854  REGULAR   48509900.0      48               25   
7   A999952066  REGULAR   32791800.0      36               15   
10  A999938479  REGULAR   60348600.0      36                5   
12  A999937745  REGULAR   42353900.0      36                6   

    Sanctioned Amount Month  Unnamed: 7  Unnamed: 8  
2            73000000  June         NaN         NaN  
5            80000000  June         NaN -19605000.0  
7            50000000  June         NaN         NaN  
10           67000000  June         NaN         NaN  
12           48000000  June         NaN         NaN

In [15]:
month_data = pd.merge(mar_data_1, jun_data, how='left', on='Loan_id', suffixes=('_mar', '_jun'))

In [16]:
month_data.head()

Loan_id Bucket_mar  TENURE_mar  PRINBALANCE_mar  Months on Books_mar  \
0  A999993387        TB0          36       14361500.0                   17   
1  A999990339        TB0          48       69805500.0                    4   
2  A999952066        TB0          36       37728800.0                   12   
3  A999937745        TB0          36       45753500.0                    3   
4  A999873098        TB0          48       42680200.0                   12   

   Sanctioned Amount_mar Month_mar  Unnamed: 7_mar  Unnamed: 8_mar  paidcure  \
0               22000000     March             NaN        576300.0         6   
1               73000000     March             NaN        848000.0         4   
2               50000000     March             NaN       1237600.0         6   
3               48000000     March             NaN             NaN         3   
4               50000000     March             NaN             NaN         6   

   paiduncure  unpaid  rollb  rollf  num6mosdel  num3mosdel  num6mosdel_2plus  \
0           0       0      0      0           0           0                 0   
1           0       0      0      0           0           0                 0   
2           0       0      0      0           0           0                 0   
3           0       1      0      0           0           0                 0   
4           0       0      0      0           0           0                 0   

   num3mosdel_2plus  max6del  max3del Month_mar Bucket_jun  PRINBALANCE_jun  \
0                 0        0        0     March        NaN              NaN   
1                 0        0        0     March    REGULAR       66303700.0   
2                 0        0        0     March    REGULAR       32791800.0   
3                 0        0        0     March    REGULAR       42353900.0   
4                 0        0        0     March    REGULAR       39679600.0   

   TENURE_jun  Months on Books_jun  Sanctioned Amount_jun Month  \
0         NaN                  NaN                    NaN   NaN   
1        48.0                  7.0             73000000.0  June   
2        36.0                 15.0             50000000.0  June   
3        36.0                  6.0             48000000.0  June   
4        48.0                 15.0             50000000.0  June   

   Unnamed: 7_jun  Unnamed: 8_jun  
0             NaN             NaN  
1             NaN             NaN  
2             NaN             NaN  
3             NaN             NaN  
4             NaN             NaN

In [17]:
month_data['Bucket_jun'].value_counts()

REGULAR    15847
TB0         1082
TB1          270
Name: Bucket_jun, dtype: int64

In [18]:
def target(row):
    if row['Bucket_jun'] == 'TB1':
        return 1
    else:
        return 0

month_data['target'] = month_data.apply(target, axis=1)

In [19]:
month_data['target'].value_counts()

0    24305
1      270
Name: target, dtype: int64

In [31]:
dups = len(month_data) - len(month_data.drop_duplicates())
month_data.info()
print('\n')
print("Number of duplicates in data frame: " + str(dups))

<class 'pandas.core.frame.DataFrame'>
Int64Index: 24575 entries, 0 to 24574
Data columns (total 30 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Loan_id                24575 non-null  object 
 1   Bucket_mar             24575 non-null  object 
 2   TENURE_mar             24575 non-null  int64  
 3   PRINBALANCE_mar        24575 non-null  float64
 4   Months on Books_mar    24575 non-null  int64  
 5   Sanctioned Amount_mar  24575 non-null  int64  
 6   Month_mar              24575 non-null  object 
 7   Unnamed: 7_mar         0 non-null      float64
 8   Unnamed: 8_mar         3 non-null      float64
 9   paidcure               24575 non-null  int64  
 10  paiduncure             24575 non-null  int64  
 11  unpaid                 24575 non-null  int64  
 12  rollb                  24575 non-null  int64  
 13  rollf                  24575 non-null  int64  
 14  num6mosdel             24575 non-null  int64  
 15  nu

In [21]:
month_data[month_data['Bucket_jun'].isnull()]

Loan_id Bucket_mar  TENURE_mar  PRINBALANCE_mar  \
0      A999993387        TB0          36     1.436150e+07   
13     A999643203        TB0          36     3.226900e+06   
19     A999349812        TB0          48     2.120330e+07   
26     A999000974        TB0          48     3.535490e+07   
30     A998901950        TB0          48     2.702210e+07   
31     A998868110        TB0          48     2.949090e+07   
32     A998840872        TB0          48     1.126823e+08   
34      A99881258        TB0          36     6.260800e+06   
37     A998762627        TB0          36     2.077180e+07   
38     A998715419        TB0          48     2.280280e+07   
45     A998582877        TB0          48     6.183700e+07   
46     A998563162        TB0          48     6.010130e+07   
50     A998455370        TB0          36     1.891550e+07   
51     A998421987        TB0          36     1.676800e+07   
52     A998379851        TB0          48     6.206420e+07   
54     A998319618        TB0          48     2.952330e+07   
56     A998215981        TB0          48     2.706230e+07   
59      A99805508        TB0          36     4.000000e+07   
60     A998049892        TB0          36     8.861600e+06   
63     A997949229        TB0          48     5.889130e+07   
65     A997892357        TB0          36     1.553980e+07   
76     A997471006        TB0          24     4.533580e+07   
79     A997341455        TB0          36     1.621030e+07   
80     A997338628        TB0          36     2.989910e+07   
83      A99730263        TB0          36     5.951600e+06   
96     A996928124        TB0          36     7.648100e+06   
101     A99677627        TB0          36     2.709900e+06   
111    A996461220        TB0          36     8.693400e+06   
112    A996411265        TB0          24     3.320980e+07   
116     A99628861        TB0          36     2.064540e+07   
126    A995895891        TB0          48     4.244620e+07   
128     A99580235        TB0          48     4.730680e+07   
133    A995651774        TB0          12     2.338680e+07   
134    A995607181        TB0          36     3.654190e+07   
135    A995598940        TB0          36     9.826500e+06   
136    A995564236        TB0          24     2.242800e+06   
137    A995504269        TB0          36     2.197530e+07   
143    A995209303        TB0          48     7.664800e+06   
145    A995175203        TB0          36     2.620700e+06   
151    A994902835        TB0          36     1.827310e+07   
152    A994885465        TB0          48     7.999075e+07   
153    A994861907        TB0          36     9.906400e+06   
161    A994697756        TB0          48     3.053290e+07   
164    A994563948        TB0          36     3.052620e+07   
166    A994506749        TB0          48     1.641030e+07   
167    A994446287        TB0          24     2.086470e+07   
169    A994389279        TB0          48     8.412910e+07   
173    A994179474        TB0          36     4.363910e+07   
177    A993988910        TB0          48     3.682160e+07   
178    A993860342        TB0          48     1.666710e+07   
179     A99383855        TB0          36     8.651400e+07   
181    A993673076        TB0          48     1.542380e+07   
183    A993664732        TB0          36     2.613360e+07   
186     A99353035        TB0          48     4.538110e+07   
192    A993253902        TB0          36     3.324920e+07   
198    A992969936        TB0          48     9.385860e+07   
201    A992926934        TB0          36     2.358110e+07   
205    A992790925        TB0          48     3.360511e+07   
206    A992787319        TB0          48     2.632100e+07   
207    A992778867        TB0          48     3.957950e+07   
210    A992685988        TB0          24     1.561870e+07   
212    A992590736        TB0          48     2.970540e+07   
216    A992420264        TB0          48     4.845390e+07   
218    A992362043        TB0          48     3.364650e+07   
219    A992306289        TB0          36     

In [22]:
month_data.loc[(month_data['Bucket_jun'].isnull()), 'Bucket_jun']='REGULAR'
# month_data['Bucket_jun'].replace('NaN', 'REGULAR', inplace=True)
month_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 24575 entries, 0 to 24574
Data columns (total 30 columns):
Loan_id                  24575 non-null object
Bucket_mar               24575 non-null object
TENURE_mar               24575 non-null int64
PRINBALANCE_mar          24575 non-null float64
Months on Books_mar      24575 non-null int64
Sanctioned Amount_mar    24575 non-null int64
Month_mar                24575 non-null object
Unnamed: 7_mar           0 non-null float64
Unnamed: 8_mar           3 non-null float64
paidcure                 24575 non-null int64
paiduncure               24575 non-null int64
unpaid                   24575 non-null int64
rollb                    24575 non-null int64
rollf                    24575 non-null int64
num6mosdel               24575 non-null int64
num3mosdel               24575 non-null int64
num6mosdel_2plus         24575 non-null int64
num3mosdel_2plus         24575 non-null int64
max6del                  24575 non-null int64
max3del         

In [27]:
month_data.columns


Index(['Loan_id', 'Bucket_mar', 'TENURE_mar', 'PRINBALANCE_mar',
       'Months on Books_mar', 'Sanctioned Amount_mar', 'Month_mar',
       'Unnamed: 7_mar', 'Unnamed: 8_mar', 'paidcure', 'paiduncure', 'unpaid',
       'rollb', 'rollf', 'num6mosdel', 'num3mosdel', 'num6mosdel_2plus',
       'num3mosdel_2plus', 'max6del', 'max3del', 'Month_mar', 'Bucket_jun',
       'PRINBALANCE_jun', 'TENURE_jun', 'Months on Books_jun',
       'Sanctioned Amount_jun', 'Month', 'Unnamed: 7_jun', 'Unnamed: 8_jun',
       'target'],
      dtype='object')

In [32]:
dataframe = month_data.drop(columns=['Unnamed: 7_mar', 'Unnamed: 8_mar', 'PRINBALANCE_jun', 'TENURE_jun', 'Months on Books_jun',
       'Sanctioned Amount_jun', 'Month', 'Unnamed: 7_jun', 'Unnamed: 8_jun'])

In [33]:
dataframe.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 24575 entries, 0 to 24574
Data columns (total 21 columns):
Loan_id                  24575 non-null object
Bucket_mar               24575 non-null object
TENURE_mar               24575 non-null int64
PRINBALANCE_mar          24575 non-null float64
Months on Books_mar      24575 non-null int64
Sanctioned Amount_mar    24575 non-null int64
Month_mar                24575 non-null object
paidcure                 24575 non-null int64
paiduncure               24575 non-null int64
unpaid                   24575 non-null int64
rollb                    24575 non-null int64
rollf                    24575 non-null int64
num6mosdel               24575 non-null int64
num3mosdel               24575 non-null int64
num6mosdel_2plus         24575 non-null int64
num3mosdel_2plus         24575 non-null int64
max6del                  24575 non-null int64
max3del                  24575 non-null int64
Month_mar                24575 non-null object
Bucket_jun 

In [57]:

features = ['TENURE_mar', 'PRINBALANCE_mar',
       'Months on Books_mar', 'Sanctioned Amount_mar', 'paidcure',
       'paiduncure', 'unpaid', 'num6mosdel', 'num3mosdel',
       'num6mosdel_2plus', 'num3mosdel_2plus', 'max6del', 'max3del',  'target']

In [58]:
dataframe[features].dtypes

TENURE_mar                 int64
PRINBALANCE_mar          float64
Months on Books_mar        int64
Sanctioned Amount_mar      int64
paidcure                   int64
paiduncure                 int64
unpaid                     int64
num6mosdel                 int64
num3mosdel                 int64
num6mosdel_2plus           int64
num3mosdel_2plus           int64
max6del                    int64
max3del                    int64
target                     int64
dtype: object

In [59]:
#Next we define 80% of the dataframe for training and 20% of the dataframe for testing.
training = dataframe.sample(frac = 0.8,random_state = 420)
X_train = training[features]
y_train = training['target']
X_test = dataframe.drop(training.index)[features]

In [70]:
X_train.describe()

TENURE_mar  PRINBALANCE_mar  Months on Books_mar  \
count  15728.000000     1.572800e+04         15728.000000   
mean      41.779629     3.356260e+07            15.680633   
std        7.477425     2.398670e+07            10.739559   
min       12.000000     5.267000e+05             0.000000   
25%       36.000000     1.756071e+07             6.000000   
50%       48.000000     2.891482e+07            14.000000   
75%       48.000000     4.395948e+07            24.000000   
max      155.000000     2.941371e+08            66.000000   

       Sanctioned Amount_mar      paidcure    paiduncure        unpaid  \
count           1.572800e+04  15728.000000  15728.000000  15728.000000   
mean            4.597302e+07      5.252416      0.039929      0.066696   
std             2.585293e+07      1.483636      0.212613      0.257529   
min             1.000000e+07      0.000000      0.000000      0.000000   
25%             3.000000e+07      5.000000      0.000000      0.000000   
50%             4.000000e+07      6.000000      0.000000      0.000000   
75%             5.500000e+07      6.000000      0.000000      0.000000   
max             3.000000e+08      6.000000      3.000000      3.000000   

         num6mosdel    num3mosdel  num6mosdel_2plus  num3mosdel_2plus  \
count  15728.000000  15728.000000      15728.000000      15728.000000   
mean       0.272889      0.212742          0.007312          0.003115   
std        0.746274      0.497605          0.151330          0.073451   
min        0.000000      0.000000          0.000000          0.000000   
25%        0.000000      0.000000          0.000000          0.000000   
50%        0.000000      0.000000          0.000000          0.000000   
75%        0.000000      0.000000          0.000000          0.000000   
max        6.000000      3.000000          6.000000          3.000000   

            max6del       max3del        target  
count  15728.000000  15728.000000  15728.000000  
mean       0.200343      0.186228      0.011190  
std        0.415852      0.398504      0.105194  
min        0.000000      0.000000      0.000000  
25%        0.000000      0.000000      0.000000  
50%        0.000000      0.000000      0.000000  
75%        0.000000      0.000000      0.000000  
max        4.000000      4.000000      1.000000

In [60]:
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC, LinearSVC
from xgboost import XGBClassifier

from sklearn.metrics import make_scorer, accuracy_score, roc_auc_score 
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split

In [61]:
#We add a validation dataset using train_test_split.
X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size = 0.2, random_state = 420)

In [62]:
#Logistic Regression
LR_Model = LogisticRegression()
LR_Model.fit(X_train, y_train)
LR_Predict = LR_Model.predict(X_valid)
LR_Accuracy = accuracy_score(y_valid, LR_Predict)
print("Accuracy: " + str(LR_Accuracy))

LR_AUC = roc_auc_score(y_valid, LR_Predict) 
print("AUC: " + str(LR_AUC))

Accuracy: 0.9885554425228891
AUC: 0.5


In [63]:
RFC_Model = RandomForestClassifier()
RFC_Model.fit(X_train, y_train)
RFC_Predict = RFC_Model.predict(X_valid)
RFC_Accuracy = accuracy_score(y_valid, RFC_Predict)
print("Accuracy: " + str(RFC_Accuracy))

RFC_AUC = roc_auc_score(y_valid, RFC_Predict) 
print("AUC: " + str(RFC_AUC))

Accuracy: 1.0
AUC: 1.0


In [73]:
XGB_Model = XGBClassifier()
XGB_Model.fit(X_train, y_train)
XGB_Predict = XGB_Model.predict(X_valid)
XGB_Accuracy = accuracy_score(y_valid, KNN_Predict)
print("Accuracy: " + str(XGB_Accuracy))

XGB_AUC = roc_auc_score(y_valid, XGB_Predict) 
print("AUC: " + str(XGB_AUC))

Accuracy: 0.9885554425228891
AUC: 1.0


In [77]:
model_performance= pd.DataFrame({'Model': ['LogisticRegression', 'RandomForestClassifier', 'XGBClassifier'],
                                            'Accuracy': [LR_Accuracy,RFC_Accuracy,XGB_Accuracy],
                                             'AUC': [LR_AUC,RFC_AUC,XGB_AUC]})
model_performance

Model  Accuracy  AUC
0      LogisticRegression  0.988555  0.5
1  RandomForestClassifier  1.000000  1.0
2           XGBClassifier  0.988555  1.0